# Descripción

Contamos con unos datasets que corresponden a un **listado de inspecciones de sanidad en locales** (Restaurantes, supermercados, etc), junto con su respectivo riesgo para la salud. Contamos con otro dataset que nos muestra una **descripción de dicho riesgo**.

**El objetivo es cargar esos datasets bajo unas especificaciones concretas y manipularlos acorde a las instrucciones de cada ejercicio.**

Todas las operaciones necesarias están descritas en los ejercicios, aunque se valorará tareas extras por propia iniciativa del alumno. También se valorará el uso del API de DataFrame.

**La entrega será un fichero zip con tu nombre y apellidos** que contendrá:
- Este fichero `ipynb`, con las correspondientes soluciones.
- Imagen del plan de ejecución del ejercicio 4.
- Descripción del plan de ejecución que podrá estar embebido en el fichero `ipynb`.

El ejercicio 10 tienes dos opciones, puedes optar por el `10a` que es continuación de este proyecto o por el `10b`

# Descargar Datasets

In [0]:
%sh 
curl -O 'https://raw.githubusercontent.com/masfworld/datahack_docker/master/zeppelin/data/food_inspections_lite.csv' --output-dir /databricks/driver
curl -O 'https://raw.githubusercontent.com/masfworld/datahack_docker/master/zeppelin/data/risk_description.csv'  --output-dir /databricks/driver

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 7361k  100 7361k    0     0  10.5M      0 --:--:-- --:--:-- --:--:-- 10.6M
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100   176  100   176    0     0    596      0 --:--:-- --:--:-- --:--:--   594


In [0]:
dbutils.fs.cp('file:/databricks/driver/food_inspections_lite.csv','dbfs:/dataset/food_inspections_lite.csv')
dbutils.fs.cp('file:/databricks/driver/risk_description.csv','dbfs:/dataset/risk_description.csv')

True

In [0]:
dbutils.fs.ls('/dataset/')

[FileInfo(path='dbfs:/dataset/Coral_cover_data.csv', name='Coral_cover_data.csv', size=5161518, modificationTime=1748072373000),
 FileInfo(path='dbfs:/dataset/OnlineRetail.csv', name='OnlineRetail.csv', size=45038728, modificationTime=1748072380000),
 FileInfo(path='dbfs:/dataset/bank.csv', name='bank.csv', size=461474, modificationTime=1746871963000),
 FileInfo(path='dbfs:/dataset/books/', name='books/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/dataset/characters.csv', name='characters.csv', size=5462, modificationTime=1747469386000),
 FileInfo(path='dbfs:/dataset/departuredelays.csv', name='departuredelays.csv', size=33396236, modificationTime=1748072375000),
 FileInfo(path='dbfs:/dataset/food_inspections_lite.csv', name='food_inspections_lite.csv', size=7538077, modificationTime=1748789816000),
 FileInfo(path='dbfs:/dataset/frankenstein.txt', name='frankenstein.txt', size=421623, modificationTime=1747469385000),
 FileInfo(path='dbfs:/dataset/loan.csv', name='loan.csv', siz

In [0]:
KAFKA_BOOSTRAP_SERVER="35.227.18.205:9094"

In [0]:
checkpoint_path = "/tmp/project_spark/_checkpoint"

In [0]:
spark.conf.set("spark.sql.streaming.checkpointLocation", checkpoint_path)
spark.conf.get("spark.sql.streaming.checkpointLocation")

'/tmp/project_spark/_checkpoint'

# Ejercicio 1
---

1. **Crea dos dataframes, uno a partir del fichero `food_inspections_lite.csv` y otro a partir de `risk_description.csv`**
2. **Convierte esos dos dataframes a tablas delta**


In [0]:
dbutils.fs.head("/dataset/food_inspections_lite.csv")

[Truncated to first 65536 bytes]


'Inspection ID,DBA Name,AKA Name,License #,Facility Type,Risk,Address,City,State,Zip,Inspection Date,Inspection Type,Results,Violations,Latitude,Longitude,Location\n2373596,COUNTY BBQ,COUNTY BBQ,2732781,Restaurant,Risk 3 (Low),1352 W TAYLOR ST ,CHICAGO,IL,60607,06/11/2020,License,Fail,,41.86945393993995,-87.66133829204541,"(-87.66133829204541, 41.86945393993995)"\n2373587,KIDZ CREATIVE CORNER,KIDZ CREATIVE CORNER,2555611,Daycare Above and Under 2 Years,Risk 1 (High),4259 N WESTERN AVE ,CHICAGO,IL,60618,06/11/2020,License Re-Inspection,Pass,,41.95944802136064,-87.68848155320953,"(-87.68848155320953, 41.95944802136064)"\n2373578,DSD DELI,DSD DELI,2626186,DELI/GROCERY,Risk 3 (Low),5205 N MILWAUKEE ,CHICAGO,IL,60630,06/11/2020,License Re-Inspection,Pass,,41.97484853157327,-87.76682905043768,"(-87.76682905043768, 41.97484853157327)"\n2373575,DSD DELI,DSD DELI,2626178,DELI/GROCERY,Risk 1 (High),5205 N MILWAUKEE ,CHICAGO,IL,60630,06/11/2020,License Re-Inspection,Pass,,41.97484853157327,-87.76

In [0]:
dbutils.fs.head("/dataset/risk_description.csv")

'risk_id,description\n1,Este riesgo significar la clausura inmediata del local\n2,Este riesgo está cerca de convertirse en la clausura del local\n3,Necesita una mejora importante\n'

In [0]:
# Parte 1 -> Crear dataframes
food_inspections_df = spark.read.format("csv") \
  .option("sep", ",") \
  .option("inferSchema", "true") \
  .option("header", "true") \
  .load("/dataset/food_inspections_lite.csv")

risk_df = spark.read.format("csv") \
  .option("sep", ",") \
  .option("inferSchema", "true") \
  .option("header", "true") \
  .load("/dataset/risk_description.csv")


In [0]:
%sql
DROP TABLE IF EXISTS food_inspections;
DROP TABLE IF EXISTS risk_descriptions;

In [0]:
dbutils.fs.rm("/user/hive/warehouse/food_inspections", recurse=True)
dbutils.fs.rm("/user/hive/warehouse/risk_descriptions", recurse=True)

False

In [0]:
# Parte 2 -> Crear tablas delta
food_inspections_df \
  .withColumnsRenamed( # No le gustan los espacios :(
    {
      "Inspection ID": "Inspection_ID",
      "DBA Name": "DBA_Name",
      "AKA Name": "AKA_Name",
      "License #": "License",
      "Facility Type": "Facility_Type",
      "Inspection Date": "Inspection_Date",
      "Inspection Type": "Inspection_Type",
    }
  ) \
  .write \
  .mode("overwrite") \
  .format("delta") \
  .saveAsTable("food_inspections")

risk_df \
  .write \
  .mode("overwrite") \
  .format("delta") \
  .saveAsTable("risk_descriptions")

In [0]:
%sql
SELECT * FROM food_inspections LIMIT 10;

Inspection_ID DBA_Name AKA_Name License Facility_Type Risk Address City State Zip Inspection_Date Inspection_Type Results Violations Latitude Longitude Location 2373596 COUNTY BBQ COUNTY BBQ 2732781 Restaurant Risk 3 (Low) 1352 W TAYLOR ST CHICAGO IL 60607 2020-06-11 License Fail null 41.86945393993995 -87.66133829204541 (-87.66133829204541, 41.86945393993995) 2373587 KIDZ CREATIVE CORNER KIDZ CREATIVE CORNER 2555611 Daycare Above and Under 2 Years Risk 1 (High) 4259 N WESTERN AVE CHICAGO IL 60618 2020-06-11 License Re-Inspection Pass null 41.95944802136064 -87.68848155320953 (-87.68848155320953, 41.95944802136064) 2373578 DSD DELI DSD DELI 2626186 DELI/GROCERY Risk 3 (Low) 5205 N MILWAUKEE CHICAGO IL 60630 2020-06-11 License Re-Inspection Pass null 41.97484853157327 -87.76682905043768 (-87.76682905043768, 41.97484853157327) 2373575 DSD DELI DSD DELI 2626178 DELI/GROCERY Risk 1 (High) 5205 N MILWAUKEE CHICAGO IL 60630 2020-06-11 License Re-Inspection Pass null 41.97484853157327 -87.76682905043768 (-87.76682905043768, 41.97484853157327) 2373576 COUNTY BBQ COUNTY BBQ 2732780 Restaurant Risk 1 (High) 1352 W TAYLOR ST CHICAGO IL 60607 2020-06-11 License Fail 3. MANAGEMENT, FOOD EMPLOYEE AND CONDITIONAL EMPLOYEE; KNOWLEDGE, RESPONSIBILITIES AND REPORTING - Comments: NO EMPLOYEE HEALTH POLICY ON PREMISES AS REQUIRED; MUST PROVIDE. INSTRUCTED THE PERSON IN CHARGE TO PROVIDE DOCUMENTATION OF EMPLOYEES RESPONSIBILITY TO REPORT ANY ILLNESS TRANSMISSIBLE THROUGH FOOD. PRIORITY FOUNDATION VIOLATION 7-38-010. | 16. FOOD-CONTACT SURFACES: CLEANED & SANITIZED - Comments: THE LOW TEMP DISH MACHINE IN THE PREP AREA IS NOT SANITIZING PROPERLY; MUST CORRECT. FOUND NO CHEMICAL READING WITH THE TEST STRIP AFTER TWO CYCLES. MACHINE MUST BE ABLE TO PROPERLY SANITIZE AT 100PPM CHLORINE. PRIORITY VIOLATION 7-38-025. | 51. PLUMBING INSTALLED; PROPER BACKFLOW DEVICES - Comments: OBSERVED THE EXPOSED HANDSINK IN THE BASEMENT PREP AREA DRAINING SLOWLY; MUST CORRECT. | 57. ALL FOOD EMPLOYEES HAVE FOOD HANDLER TRAINING - Comments: INSTRUCTED THE PERSON IN CHARGE THAT ALL FOOD HANDLERS MUST OBTAIN THE REQUIRED FOOD HANDLER TRAINING. 41.86945393993995 -87.66133829204541 (-87.66133829204541, 41.86945393993995) 2373547 NEW SEOUL NEW SEOUL 62062 null Risk 3 (Low) 5351 N LINCOLN AVE CHICAGO IL 60625 2020-06-11 Canvass Out of Business null 41.97923607630261 -87.69252686676323 (-87.69252686676323, 41.97923607630261) 2373543 CAFE UTJEHA, INC. CAFE UTJEHA 1592606 Restaurant Risk 2 (Medium) 5350 N LINCOLN AVE CHICAGO IL 60625 2020-06-11 Canvass Pass w/ Conditions 2. CITY OF CHICAGO FOOD SERVICE SANITATION CERTIFICATE - Comments: NO CITY OF CHICAGO CERTIFIED FOOD MANAGER ON SITE DURING THE INSPECTION WHILE THE TEMPERATURE CONTROL FOR SAFETY FOODS (MILK) HAS BEEN PREPARED AND SERVED. INSTRUCTED A CITY OF CHICAGO CERTIFIED FOOD MANAGER MUST BE ON SITE AT ALL TIMES FOODS ARE BEING PREPARED AND SERVED. PRIORITY FOUNDATION VIOLATION 7-38-012.CITATION ISSUED | 3. MANAGEMENT, FOOD EMPLOYEE AND CONDITIONAL EMPLOYEE; KNOWLEDGE, RESPONSIBILITIES AND REPORTING - Comments: MANAGER PROVIDED NO PROOF OF EMPLOYEE HEALTH POLICY ON SITE. INSTRUCTED TO PROVIDE AN EMPLOYEE HEALTH POLICY THAT INCLUDES A SIGNED ACKNOWLEDGEMENT FROM EACH EMPLOYEE. PRIORITY FOUNDATION. 7.38.010. NO CITATION ISSUED. | 36. THERMOMETERS PROVIDED & ACCURATE - Comments: OBSERVED NO PROBE THERMOMETER FOR TAKING FOOD TEMPERATURES.MUST PROVIDE.(PRIORITY FOUNDATION-NO CITATION ISSUED) 7-38-005 | 44. UTENSILS, EQUIPMENT & LINENS: PROPERLY STORED, DRIED, & HANDLED - Comments: MUST REMOVE SINGLE SERVICE FOOD UTENSILS AND CUPS STORED IN KITCHEN CABINETS UNDER HAND WASHING SINK | 51. PLUMBING INSTALLED; PROPER BACKFLOW DEVICES - Comments: BACKFLOW PREVENTION DEVICES NOT LOCATED CAPPUCCINO/ESPRESSO MACHINE. MUST INSTALL BACKFLOW PREVENTION DEVICES OR AIR GAP BETWEEN THE WATER SUPPLY INLET AND THE UNIT SO IT MAY BE LOCATED TO BE SERVICED AND MAINTAINED | 55. PHYSICAL FACILITIES INSTALLED, MAINTAINED & CLEAN - Comments: OBSE

In [0]:
%sql
SELECT * FROM risk_descriptions LIMIT 10;

risk_id description 1 Este riesgo significar la clausura inmediata del local 2 Este riesgo está cerca de convertirse en la clausura del local 3 Necesita una mejora importante

# Ejercicio 2
**Obtén el número de inspecciones distintas con Riesgo alto `Risk 1 (High)`**

---



In [0]:
from pyspark.sql.functions import col

# Se asume que cada inspección es distinta
food_inspections_df \
  .filter(food_inspections_df.Risk == "Risk 1 (High)") \
  .groupBy(col("Risk")) \
  .count() \
  .select(
    col("Risk"),
    col("count").alias("number")
  ).display()


Risk number Risk 1 (High) 7215


# Ejercicio 3
**A partir de los dataframes cargados anteriormente, obtén una tabla con las siguientes columnas:<br>**
1. `DBA Name`
2. `Facility Type`
3. `Risk`
4. `Risk description`

---

In [0]:
# Esto nos sirve para ver lo que nos encontramos en la columna Risk y tenerlo en cuenta en el siguiente.

food_inspections_df \
  .select(food_inspections_df.Risk) \
  .distinct().display()

Risk null Risk 1 (High) All Risk 2 (Medium) Risk 3 (Low)

In [0]:
# Tenemos que hacer un join de los dos dataframes, pero necesitamos formatear el nivel de riesgo para encajar con el segundo
# Se pueden usar funciones que ya existen pero por mostrar otro elemento que hemos visto en clase, vamos a crear una udf

from pyspark.sql.functions import col, udf

@udf()
def get_risk_level(risk):
  if risk is not None:
    return risk.split(" ")[1] # segunda "palabra" [Risk, 1, (High)]

# No se menciona nada de ordenar, nos lo ahorramos y evitamos shuffle innecesario

food_inspections_df \
  .na.drop(subset=["Risk"]) \
  .filter(food_inspections_df.Risk != "All") \
  .withColumn("risk_level", get_risk_level(col("Risk"))) \
  .join(risk_df, col("risk_level") == risk_df.risk_id) \
  .select(
    food_inspections_df["DBA Name"],
    food_inspections_df["Facility Type"],
    col("Risk"),
    risk_df["description"].alias("Risk description")
  ).display()

DBA Name Facility Type Risk Risk description COUNTY BBQ Restaurant Risk 3 (Low) Necesita una mejora importante KIDZ CREATIVE CORNER Daycare Above and Under 2 Years Risk 1 (High) Este riesgo significar la clausura inmediata del local DSD DELI DELI/GROCERY Risk 3 (Low) Necesita una mejora importante DSD DELI DELI/GROCERY Risk 1 (High) Este riesgo significar la clausura inmediata del local COUNTY BBQ Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local NEW SEOUL null Risk 3 (Low) Necesita una mejora importante CAFE UTJEHA, INC. Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local MARATHON GAS Grocery Store Risk 3 (Low) Necesita una mejora importante HALSTED BOWL Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local HAROLD'S CHICKEN Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local HYATT HOUSE/HYATT PLACE AND FOOD CT HOTEL Risk 3 (Low) Necesita una mejora importante ARBY'S ROAST BEEF Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local LOS ENCINOS INC. Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local HYATT HOUSE/HYATT PLAXE AND FOOD CT null Risk 1 (High) Este riesgo significar la clausura inmediata del local MAYFAIR RESTAURANT Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local JJ PEPPERS FOOD STORE Grocery Store Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local RAMEN-SAN DELUXE/ TALLBOY TACO Restaurant Risk 3 (Low) Necesita una mejora importante RAMEN-SAN DELUXE/ TALLBOY TACO Restaurant Risk 3 (Low) Necesita una mejora importante RAMEN-SAN DELUXE/ TALLBOY TACO Restaurant Risk 3 (Low) Necesita una mejora importante MORGANS ON FULTON Restaurant Risk 3 (Low) Necesita una mejora importante DUNKIN DONUTS & BASKIN ROBINS Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local MARI'S BUMBLE BEE DAY CARE CORP. Daycare Above and Under 2 Years Risk 1 (High) Este riesgo significar la clausura inmediata del local WINGSTOP Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local PRAIRIELAND MONTESSORI Daycare (2 - 6 Years) Risk 1 (High) Este riesgo significar la clausura inmediata del local MCDONALD'S Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local CHIPOTLE MEXICAN GRILL #3481 Restaurant Risk 3 (Low) Necesita una mejora importante CHIPOTLE MEXICAN GRILL #3481 Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local THE HANA CENTER Children's Services Facility Risk 1 (High) Este riesgo significar la clausura inmediata del local CVS/PHARMACY #4061 convenience/drug store Risk 3 (Low) Necesita una mejora importante SUBWAY Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local Northwest Middle/Belmont-Cragin School Risk 1 (High) Este riesgo significar la clausura inmediata del local MAYFAIR RESTAURANT Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local CHARLES CARROLL ELEMENTARY School Risk 1 (High) Este riesgo significar la clausura inmediata del local COPPER CIRCLE Restaurant Risk 2 (Medium) Este riesgo está cerca de convertirse en la clausura del local GATEWAY NEWSTANDS Grocery Store Risk 3 (Low) Necesita una mejora importante SLIMS Restaurant Risk 1 (High) Este riesgo significar la clausura inmediata del local ARCHER DISCOUNT STORE null Risk 3 (Low) Necesita una mejora importante JACOB BEIDLER ELEMENTARY SCHOOL School Risk 1 (High) Este riesgo significar la clausura inmediata del local DOLLAR GENERAL STORE19101 Grocery Store Risk 3 (Low) Necesita una mejora importante CENTERS FOR NEW HORIZONS AT DAWSON TECHNICAL INSTITUTE Daycare Above and Under 2 Years Risk 1 (High) Este riesgo significar la clausura inmediata del local GERALD DELGADO KANOON ELEMENTARY School Risk 1 (High) Este riesgo significar la clausura inm

# Ejercicio 4
**Accede a la Spark UI para ver el plan de ejecución. Describe cada una de las piezas/cajas que componen el plan de ejecución (Una descripción breve de una línea por caja será suficiente).**<br><br>**Recordad hacer un pantallazo del plan de ejecución analizado**

---



Vamos de abajo a arriba en la captura de pantalla `plan_ejecucion_sergio_yunta.png`:

1. Vemos abajo del todo la parte del plan correspondiente a la lectura del csv al que hace referencia `food_inspections_df` y el filtro de los valores nulos de la columna risk **junto** con el filtrado de los valores `"All"`. De momento no hay shuffle porque es una operación del filtrado.
2. Seguimos el camino y llegamos a la evaluación de nuestra UDF `get_risk_level` (representado por `BatchEvalPython`) que se forma de un filtrado de nulos (el `if ... is not None`) y una proyección de valores. Posteriormente nos indica que se vuelve a evaluar antes de la proyección para agregar una columna "auxiliar" para hacer el join a continuación.
3. En la parte de la derecha, vemos de nuevo una lectura de csv de `risk_df` donde también automáticamente hace un filtrado de nulos.
4. Pasamos al join, vemos que como era de esperar es de tipo `Broadcast Hash Join` ya que la segunda tabla (`risk_df`) es muy pequeña y por tamaño es más eficiente replicarla en todos los nodos.
5. Por último, hay una proyección de las columnas que se piden en el enunciado. Las cajas que quedan son utilidades de spark como el plan de ejecución adaptativo y las optimizaciones que realiza de forma automática.

# Ejercicio 5
**1. Obtén el número de inspecciones para cada local (columna `DBA Name`) y su resultado (columna `Results`).**<br><br>
**2. Obtén las dos locales (`DBA Name`) que más inspecciones han tenido por cada uno de los resultados**<br><br>
**3. Guarda los resultados en una nueva tabla Delta llamada `inspections_results`**

---

In [0]:
# Esto nos sirve para ver lo que nos encontramos en la columna Risk y tenerlo en cuenta en el siguiente.

food_inspections_df \
  .select(food_inspections_df.Results) \
  .distinct().display()

Results Not Ready Fail No Entry Business Not Located Pass w/ Conditions Out of Business Pass

In [0]:
from pyspark.sql.functions import col

# Primer paso, obtener el número de inspecciones por local y resultado

inspections_grouped = food_inspections_df \
  .groupBy(
    food_inspections_df["DBA Name"],
    food_inspections_df["Results"]
  ) \
  .count() \
  .select(
    food_inspections_df["DBA Name"],
    col("count").alias("Num inspections"),
    food_inspections_df["Results"]
  )

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import col, row_number, desc

# Segundo paso, mediante window partitioning obtenemos el top dos de locales por result

by_result = Window.partitionBy("Results").orderBy(desc("Num inspections"))

inspections_results_df = inspections_grouped \
  .withColumn("inspection_row_num", row_number().over(by_result)) \
  .filter(col("inspection_row_num") <= 2) \
  .select(
    inspections_grouped["DBA Name"],
    inspections_grouped["Num inspections"],
    inspections_grouped["Results"],
  )

inspections_results_df.display()

DBA Name Num inspections Results RICE THAI CAFE 1 Business Not Located CHINA STATION 1 Business Not Located SUBWAY 10 Fail DUNKIN DONUTS 5 Fail LANS 5 No Entry LA PENA RESTAURANTE 4 No Entry PALETERIA Y NEVERIA LA MEXICANA YOGURT AND CHURRO 5 Not Ready SUBWAY 4 Not Ready SUBWAY 16 Out of Business DUNKIN DONUTS 10 Out of Business SUBWAY 100 Pass DUNKIN DONUTS 42 Pass SUBWAY 11 Pass w/ Conditions DUNKIN DONUTS 7 Pass w/ Conditions

In [0]:
%sql
DROP TABLE IF EXISTS inspections_results

In [0]:
dbutils.fs.rm("/user/hive/warehouse/inspections_results", recurse=True)

False

In [0]:
# Tercer paso, transformarlo en la tabla delta
inspections_results_df \
  .withColumnsRenamed( # No le gustan los espacios :(
    {
      "DBA Name": "DBA_Name",
      "Num inspections": "Num_inspections",
    }
  ) \
  .write \
  .mode("overwrite") \
  .format("delta") \
  .saveAsTable("inspections_results")

In [0]:
%sql
SELECT * FROM inspections_results

DBA_Name Num_inspections Results RICE THAI CAFE 1 Business Not Located CHINA STATION 1 Business Not Located SUBWAY 10 Fail DUNKIN DONUTS 5 Fail LANS 5 No Entry LA PENA RESTAURANTE 4 No Entry PALETERIA Y NEVERIA LA MEXICANA YOGURT AND CHURRO 5 Not Ready SUBWAY 4 Not Ready SUBWAY 16 Out of Business DUNKIN DONUTS 10 Out of Business SUBWAY 100 Pass DUNKIN DONUTS 42 Pass SUBWAY 11 Pass w/ Conditions DUNKIN DONUTS 7 Pass w/ Conditions

# Ejercicio 6
1. **Actualiza la tabla delta creada en el ejercicio anterios, con el valor `DBA_Name = "error"`**
2. **Restaura la tabla a su estado original**

---



In [0]:
from delta.tables import DeltaTable
from pyspark.sql.functions import lit

inspections_results_table = DeltaTable.forName(spark, "inspections_results")

inspections_results_table.update(set = { "DBA_Name": lit("error") } )

In [0]:
%sql
SELECT * FROM inspections_results

DBA_Name Num_inspections Results error 1 Business Not Located error 1 Business Not Located error 10 Fail error 5 Fail error 5 No Entry error 4 No Entry error 5 Not Ready error 4 Not Ready error 16 Out of Business error 10 Out of Business error 100 Pass error 42 Pass error 11 Pass w/ Conditions error 7 Pass w/ Conditions

In [0]:
%sql
DESCRIBE HISTORY inspections_results

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 1 2025-06-01T15:00:32Z 7726499663423251 sergio.yunta@hotmail.com UPDATE Map(predicate -> []) null List(4402192642578873) 0601-134109-24xz8dde 0 WriteSerializable false Map(numRemovedFiles -> 1, numRemovedBytes -> 1631, numCopiedRows -> 0, numDeletionVectorsAdded -> 0, numDeletionVectorsRemoved -> 0, numAddedChangeFiles -> 0, executionTimeMs -> 677, numDeletionVectorsUpdated -> 0, scanTimeMs -> 62, numAddedFiles -> 1, numUpdatedRows -> 14, numAddedBytes -> 1480, rewriteTimeMs -> 615) null Databricks-Runtime/15.4.x-scala2.12 0 2025-06-01T15:00:20Z 7726499663423251 sergio.yunta@hotmail.com CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {}, statsOnLoad -> false) null List(4402192642578873) 0601-134109-24xz8dde null WriteSerializable false Map(numFiles -> 1, numOutputRows -> 14, numOutputBytes -> 1631) null Databricks-Runtime/15.4.x-scala2.12

In [0]:
inspections_results_table.restoreToVersion(0)

DataFrame[table_size_after_restore: bigint, num_of_files_after_restore: bigint, num_removed_files: bigint, num_restored_files: bigint, removed_files_size: bigint, restored_files_size: bigint]

In [0]:
%sql
SELECT * FROM inspections_results

DBA_Name Num_inspections Results RICE THAI CAFE 1 Business Not Located CHINA STATION 1 Business Not Located SUBWAY 10 Fail DUNKIN DONUTS 5 Fail LANS 5 No Entry LA PENA RESTAURANTE 4 No Entry PALETERIA Y NEVERIA LA MEXICANA YOGURT AND CHURRO 5 Not Ready SUBWAY 4 Not Ready SUBWAY 16 Out of Business DUNKIN DONUTS 10 Out of Business SUBWAY 100 Pass DUNKIN DONUTS 42 Pass SUBWAY 11 Pass w/ Conditions DUNKIN DONUTS 7 Pass w/ Conditions

# Ejercicio 7

**Crea una aplicación son Structured Streaming que lea los datos del topic de Kafka `inspections`. La url del servidor Kafka está definida al comienzo de este notebook**

**Los datos procedentes de este topic son exactamente los mismos que estamos analizando durante todo este notebook, `Food Inspections`, así que el esquema es el mismo**

In [0]:
# Utilidad para resetear el checkpoint
checkpoint_path = "/tmp/project_spark/_checkpoint"

dbutils.fs.rm(checkpoint_path, True)

spark.conf.set("spark.sql.streaming.checkpointLocation", checkpoint_path)
spark.conf.get("spark.sql.streaming.checkpointLocation")

'/tmp/project_spark/_checkpoint'

In [0]:
KAFKA_BOOSTRAP_SERVER="35.227.18.205:9094"

In [0]:
from pyspark.sql.functions import from_json, col, to_date
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DateType, DoubleType
# Si no le añadimos la opción maxOffsetsPerTrigger, explota :(
inspections_kafka_df = spark \
  .readStream \
  .format("kafka") \
  .option("kafka.bootstrap.servers", KAFKA_BOOSTRAP_SERVER) \
  .option("subscribe", "inspections") \
  .option("startingOffsets", "earliest") \
  .option("maxOffsetsPerTrigger", 500) \
  .load()

"""
Esto es interesante, el esquema del ejercicio 1 no nos sirve (los tipos de datos) porque los mensajes de kafka vienen
todos con String, por lo que si ponemos otros tipos de datos que no sean string en el schema, 
vamos a tener como resultado null en dichas columnas.

Lo dejamos como string todos, y realizamos el casting luego.
"""

schema = StructType(
    [
        StructField('Inspection ID', StringType(), True),
        StructField('DBA Name', StringType(), True),
        StructField('AKA Name', StringType(), True),
        StructField('License #', StringType(), True),
        StructField('Facility Type', StringType(), True),
        StructField('Risk', StringType(), True),
        StructField('Address', StringType(), True),
        StructField('City', StringType(), True),
        StructField('State', StringType(), True),
        StructField('Zip', StringType(), True),
        StructField('Inspection Date', StringType(), True),
        StructField('Inspection Type', StringType(), True),
        StructField('Results', StringType(), True),
        StructField('Violations', StringType(), True),
        StructField('Latitude', StringType(), True),
        StructField('Longitude', StringType(), True),
        StructField('Location', StringType(), True),
    ]
)
inspections_stream = inspections_kafka_df \
  .selectExpr("CAST(value AS STRING)", "timestamp") \
  .withColumn("value", from_json("value", schema)) \
  .select(col('value.*'), col("timestamp")) \
  .withColumn("Inspection ID", col("Inspection ID").cast("int")) \
  .withColumn("License #", col("License #").cast("int")) \
  .withColumn("Zip", col("Zip").cast("int")) \
  .withColumn("Latitude", col("Latitude").cast("double")) \
  .withColumn("Longitude", col("Longitude").cast("double")) \
  .withColumn("Inspection Date", to_date(col("Inspection Date"), "MM/dd/yyyy"))

In [0]:
inspections_stream.display()

Inspection ID DBA Name AKA Name License # Facility Type Risk Address City State Zip Inspection Date Inspection Type Results Violations Latitude Longitude Location timestamp 2373596 COUNTY BBQ COUNTY BBQ 2732781 Restaurant Risk 3 (Low) 1352 W TAYLOR ST CHICAGO IL 60607 2020-06-11 License Fail 41.86945393993995 -87.66133829204541 (-87.66133829204541, 41.86945393993995) 2025-05-18T16:47:28.588Z 2373587 KIDZ CREATIVE CORNER KIDZ CREATIVE CORNER 2555611 Daycare Above and Under 2 Years Risk 1 (High) 4259 N WESTERN AVE CHICAGO IL 60618 2020-06-11 License Re-Inspection Pass 41.95944802136064 -87.68848155320953 (-87.68848155320953, 41.95944802136064) 2025-05-18T16:47:28.598Z 2373578 DSD DELI DSD DELI 2626186 DELI/GROCERY Risk 3 (Low) 5205 N MILWAUKEE CHICAGO IL 60630 2020-06-11 License Re-Inspection Pass 41.97484853157327 -87.76682905043768 (-87.76682905043768, 41.97484853157327) 2025-05-18T16:47:28.607Z 2373575 DSD DELI DSD DELI 2626178 DELI/GROCERY Risk 1 (High) 5205 N MILWAUKEE CHICAGO IL 60630 2020-06-11 License Re-Inspection Pass 41.97484853157327 -87.76682905043768 (-87.76682905043768, 41.97484853157327) 2025-05-18T16:47:28.613Z 2373576 COUNTY BBQ COUNTY BBQ 2732780 Restaurant Risk 1 (High) 1352 W TAYLOR ST CHICAGO IL 60607 2020-06-11 License Fail 3. MANAGEMENT, FOOD EMPLOYEE AND CONDITIONAL EMPLOYEE; KNOWLEDGE, RESPONSIBILITIES AND REPORTING - Comments: NO EMPLOYEE HEALTH POLICY ON PREMISES AS REQUIRED; MUST PROVIDE. INSTRUCTED THE PERSON IN CHARGE TO PROVIDE DOCUMENTATION OF EMPLOYEES RESPONSIBILITY TO REPORT ANY ILLNESS TRANSMISSIBLE THROUGH FOOD. PRIORITY FOUNDATION VIOLATION 7-38-010. | 16. FOOD-CONTACT SURFACES: CLEANED & SANITIZED - Comments: THE LOW TEMP DISH MACHINE IN THE PREP AREA IS NOT SANITIZING PROPERLY; MUST CORRECT. FOUND NO CHEMICAL READING WITH THE TEST STRIP AFTER TWO CYCLES. MACHINE MUST BE ABLE TO PROPERLY SANITIZE AT 100PPM CHLORINE. PRIORITY VIOLATION 7-38-025. | 51. PLUMBING INSTALLED; PROPER BACKFLOW DEVICES - Comments: OBSERVED THE EXPOSED HANDSINK IN THE BASEMENT PREP AREA DRAINING SLOWLY; MUST CORRECT. | 57. ALL FOOD EMPLOYEES HAVE FOOD HANDLER TRAINING - Comments: INSTRUCTED THE PERSON IN CHARGE THAT ALL FOOD HANDLERS MUST OBTAIN THE REQUIRED FOOD HANDLER TRAINING. 41.86945393993995 -87.66133829204541 (-87.66133829204541, 41.86945393993995) 2025-05-18T16:47:28.623Z 2373547 NEW SEOUL NEW SEOUL 62062 Risk 3 (Low) 5351 N LINCOLN AVE CHICAGO IL 60625 2020-06-11 Canvass Out of Business 41.97923607630261 -87.69252686676323 (-87.69252686676323, 41.97923607630261) 2025-05-18T16:47:28.637Z 2373543 CAFE UTJEHA, INC. CAFE UTJEHA 1592606 Restaurant Risk 2 (Medium) 5350 N LINCOLN AVE CHICAGO IL 60625 2020-06-11 Canvass Pass w/ Conditions 2. CITY OF CHICAGO FOOD SERVICE SANITATION CERTIFICATE - Comments: NO CITY OF CHICAGO CERTIFIED FOOD MANAGER ON SITE DURING THE INSPECTION WHILE THE TEMPERATURE CONTROL FOR SAFETY FOODS (MILK) HAS BEEN PREPARED AND SERVED. INSTRUCTED A CITY OF CHICAGO CERTIFIED FOOD MANAGER MUST BE ON SITE AT ALL TIMES FOODS ARE BEING PREPARED AND SERVED. PRIORITY FOUNDATION VIOLATION 7-38-012.CITATION ISSUED | 3. MANAGEMENT, FOOD EMPLOYEE AND CONDITIONAL EMPLOYEE; KNOWLEDGE, RESPONSIBILITIES AND REPORTING - Comments: MANAGER PROVIDED NO PROOF OF EMPLOYEE HEALTH POLICY ON SITE. INSTRUCTED TO PROVIDE AN EMPLOYEE HEALTH POLICY THAT INCLUDES A SIGNED ACKNOWLEDGEMENT FROM EACH EMPLOYEE. PRIORITY FOUNDATION. 7.38.010. NO CITATION ISSUED. | 36. THERMOMETERS PROVIDED & ACCURATE - Comments: OBSERVED NO PROBE THERMOMETER FOR TAKING FOOD TEMPERATURES.MUST PROVIDE.(PRIORITY FOUNDATION-NO CITATION ISSUED) 7-38-005 | 44. UTENSILS, EQUIPMENT & LINENS: PROPERLY STORED, DRIED, & HANDLED - Comments: MUST REMOVE SINGLE SERVICE FOOD UTENSILS AND CUPS STORED IN KITCHEN CABINETS UNDER HAND WASHING SINK | 51. PLUMBING INSTALLED; PROPER BACKFLOW DEVICES - Comments: BACKFLOW PREVENTION DEVICES NOT LOCATED CAPPUCCINO/ESPRESSO MACHINE. MUST INSTALL BACKFLOW PREVENTION DEVICES OR AIR GAP BETWEEN THE WATER SUPPLY INLET AND 

# Ejercicio 8
**En base a la fuente de datos del ejercicio anterior, obtén cada 5 segundos el número de inspecciones por `Facility Type`**

In [0]:
# Utilidad para resetear el checkpoint
checkpoint_path = "/tmp/project_spark/_checkpoint"

dbutils.fs.rm(checkpoint_path, True)

spark.conf.set("spark.sql.streaming.checkpointLocation", checkpoint_path)
spark.conf.get("spark.sql.streaming.checkpointLocation")

'/tmp/project_spark/_checkpoint'

In [0]:
from pyspark.sql.functions import window

grouped_by_facility = inspections_stream \
  .groupBy(
    window(col("timestamp"), "5 seconds"),
    col("Facility Type")
  ).count()

In [0]:
grouped_by_facility.display()

window Facility Type count List(2025-05-18T17:23:15Z, 2025-05-18T17:23:20Z) Grocery Store 3 List(2025-05-18T16:57:45Z, 2025-05-18T16:57:50Z) Restaurant 7 List(2025-05-18T17:02:45Z, 2025-05-18T17:02:50Z) School 1 List(2025-05-18T16:59:25Z, 2025-05-18T16:59:30Z) Grocery Store 1 List(2025-05-18T16:47:45Z, 2025-05-18T16:47:50Z) Grocery Store 1 List(2025-05-18T17:24:55Z, 2025-05-18T17:25:00Z) Restaurant 6 List(2025-05-18T17:13:15Z, 2025-05-18T17:13:20Z) Grocery Store 1 List(2025-05-18T16:56:45Z, 2025-05-18T16:56:50Z) Grocery Store 3 List(2025-05-18T17:29:55Z, 2025-05-18T17:30:00Z) Grocery Store 2 List(2025-05-18T17:31:55Z, 2025-05-18T17:32:00Z) Restaurant 8 List(2025-05-18T17:13:55Z, 2025-05-18T17:14:00Z) Restaurant 2 List(2025-05-18T16:59:05Z, 2025-05-18T16:59:10Z) Grocery Store 3 List(2025-05-18T17:19:55Z, 2025-05-18T17:20:00Z) Restaurant 5 List(2025-05-18T17:21:55Z, 2025-05-18T17:22:00Z) 1 List(2025-05-18T16:58:25Z, 2025-05-18T16:58:30Z) Grocery Store 3 List(2025-05-18T16:59:05Z, 2025-05-18T16:59:10Z) Restaurant 5 List(2025-05-18T16:59:05Z, 2025-05-18T16:59:10Z) School 1 List(2025-05-18T17:10:55Z, 2025-05-18T17:11:00Z) Restaurant 5 List(2025-05-18T17:00:45Z, 2025-05-18T17:00:50Z) Daycare Above and Under 2 Years 1 List(2025-05-18T17:10:55Z, 2025-05-18T17:11:00Z) Daycare Above and Under 2 Years 1 List(2025-05-18T17:02:45Z, 2025-05-18T17:02:50Z) Restaurant 4 List(2025-05-18T17:19:15Z, 2025-05-18T17:19:20Z) Restaurant 7 List(2025-05-18T17:23:55Z, 2025-05-18T17:24:00Z) Grocery Store 2 List(2025-05-18T17:18:35Z, 2025-05-18T17:18:40Z) Restaurant 4 List(2025-05-18T16:56:45Z, 2025-05-18T16:56:50Z) School 1 List(2025-05-18T17:00:45Z, 2025-05-18T17:00:50Z) Grocery Store 4 List(2025-05-18T17:16:55Z, 2025-05-18T17:17:00Z) 1 List(2025-05-18T17:10:55Z, 2025-05-18T17:11:00Z) Grocery Store 1 List(2025-05-18T17:25:15Z, 2025-05-18T17:25:20Z) Grocery Store 5 List(2025-05-18T17:26:55Z, 2025-05-18T17:27:00Z) Shared Kitchen User (Short Term) 1 List(2025-05-18T17:23:35Z, 2025-05-18T17:23:40Z) Grocery Store 2 List(2025-05-18T17:28:55Z, 2025-05-18T17:29:00Z) Grocery Store 1 List(2025-05-18T16:59:25Z, 2025-05-18T16:59:30Z) HOTEL 2 List(2025-05-18T17:14:55Z, 2025-05-18T17:15:00Z) Restaurant 5 List(2025-05-18T16:59:25Z, 2025-05-18T16:59:30Z) Restaurant 6 List(2025-05-18T16:58:05Z, 2025-05-18T16:58:10Z) School 2 List(2025-05-18T17:26:35Z, 2025-05-18T17:26:40Z) Grocery Store 1 List(2025-05-18T17:15:15Z, 2025-05-18T17:15:20Z) HOTEL 2 List(2025-05-18T17:15:15Z, 2025-05-18T17:15:20Z) Restaurant 6 List(2025-05-18T16:56:05Z, 2025-05-18T16:56:10Z) Daycare Above and Under 2 Years 1 List(2025-05-18T17:26:55Z, 2025-05-18T17:27:00Z) Restaurant 4 List(2025-05-18T17:32:55Z, 2025-05-18T17:33:00Z) Shelter 1 List(2025-05-18T17:28:35Z, 2025-05-18T17:28:40Z) Restaurant 8 List(2025-05-18T17:21:55Z, 2025-05-18T17:22:00Z) Bakery 1 List(2025-05-18T17:27:35Z, 2025-05-18T17:27:40Z) Mobile Frozen Desserts Vendor 1 List(2025-05-18T17:16:35Z, 2025-05-18T17:16:40Z) Restaurant 5 List(2025-05-18T17:02:05Z, 2025-05-18T17:02:10Z) Grocery Store 3 List(2025-05-18T17:14:35Z, 2025-05-18T17:14:40Z) Restaurant 1 List(2025-05-18T16:58:45Z, 2025-05-18T16:58:50Z) Grocery Store 6 List(2025-05-18T16:57:25Z, 2025-05-18T16:57:30Z) Mobile Prepared Food Vendor 2 List(2025-05-18T17:34:55Z, 2025-05-18T17:35:00Z) Restaurant 8 List(2025-05-18T17:20:55Z, 2025-05-18T17:21:00Z) Bakery 1 List(2025-05-18T17:27:15Z, 2025-05-18T17:27:20Z) Restaurant 7 List(2025-05-18T16:55:25Z, 2025-05-18T16:55:30Z) Grocery Store 1 List(2025-05-18T16:57:25Z, 2025-05-18T16:57:30Z) Grocery Store 1 List(2025-05-18T17:17:55Z, 2025-05-18T17:18:00Z) Bakery 2 List(2025-05-18T17:00:05Z, 2025-05-18T17:00:10Z) Grocery Store 5 List(2025-05-18T17:26:55Z, 2025-05-18T17:27:00Z) Catering 1 List(2025-05-18T16:57:45Z, 2025-05-18T16:57:50Z) Grocery Store 3 List(2025-05-18T16:47:45Z, 2025-05-18T16:47:50Z) Restaurant 7 List(2025-05-18T17:27:15Z, 2025-05-18T17:27:20Z) Children's Services Facility 1 List(2025-05-18T17:29:55Z, 2025-05-18T17:30:00Z) Resta

# Ejercicio 9
**En base a la fuente de datos del ejercicio 7, obtén cada 5 segundos el número de inspecciones por `Results` de los últimos 30 segundos**

In [0]:
# Utilidad para resetear el checkpoint
checkpoint_path = "/tmp/project_spark/_checkpoint"

dbutils.fs.rm(checkpoint_path, True)

spark.conf.set("spark.sql.streaming.checkpointLocation", checkpoint_path)
spark.conf.get("spark.sql.streaming.checkpointLocation")

'/tmp/project_spark/_checkpoint'

In [0]:
grouped_by_results = inspections_stream.groupBy(
  window(col("timestamp"), "30 seconds", "5 seconds"),
  col("Results")
).count()

In [0]:
grouped_by_results.display()

window Results count List(2025-05-18T17:29:30Z, 2025-05-18T17:30:00Z) Pass w/ Conditions 4 List(2025-05-18T17:31:15Z, 2025-05-18T17:31:45Z) No Entry 2 List(2025-05-18T17:25:55Z, 2025-05-18T17:26:25Z) Pass w/ Conditions 3 List(2025-05-18T16:57:25Z, 2025-05-18T16:57:55Z) Pass 13 List(2025-05-18T17:24:20Z, 2025-05-18T17:24:50Z) Out of Business 2 List(2025-05-18T16:55:15Z, 2025-05-18T16:55:45Z) Not Ready 1 List(2025-05-18T17:32:15Z, 2025-05-18T17:32:45Z) Pass 7 List(2025-05-18T17:22:30Z, 2025-05-18T17:23:00Z) Out of Business 5 List(2025-05-18T17:30:55Z, 2025-05-18T17:31:25Z) Pass 15 List(2025-05-18T17:29:55Z, 2025-05-18T17:30:25Z) Pass w/ Conditions 3 List(2025-05-18T17:02:25Z, 2025-05-18T17:02:55Z) Pass 9 List(2025-05-18T17:18:55Z, 2025-05-18T17:19:25Z) Fail 1 List(2025-05-18T16:58:25Z, 2025-05-18T16:58:55Z) Pass 12 List(2025-05-18T17:24:10Z, 2025-05-18T17:24:40Z) Pass 3 List(2025-05-18T17:12:10Z, 2025-05-18T17:12:40Z) Pass w/ Conditions 2 List(2025-05-18T17:01:30Z, 2025-05-18T17:02:00Z) Out of Business 4 List(2025-05-18T16:58:40Z, 2025-05-18T16:59:10Z) Fail 1 List(2025-05-18T17:22:20Z, 2025-05-18T17:22:50Z) Out of Business 1 List(2025-05-18T17:14:15Z, 2025-05-18T17:14:45Z) Not Ready 2 List(2025-05-18T17:30:50Z, 2025-05-18T17:31:20Z) No Entry 3 List(2025-05-18T16:47:00Z, 2025-05-18T16:47:30Z) Pass 3 List(2025-05-18T17:25:20Z, 2025-05-18T17:25:50Z) Fail 1 List(2025-05-18T17:19:20Z, 2025-05-18T17:19:50Z) Fail 1 List(2025-05-18T17:28:25Z, 2025-05-18T17:28:55Z) Fail 3 List(2025-05-18T17:16:15Z, 2025-05-18T17:16:45Z) No Entry 1 List(2025-05-18T17:22:20Z, 2025-05-18T17:22:50Z) Fail 1 List(2025-05-18T17:14:40Z, 2025-05-18T17:15:10Z) Pass w/ Conditions 2 List(2025-05-18T16:48:05Z, 2025-05-18T16:48:35Z) Pass 6 List(2025-05-18T17:13:30Z, 2025-05-18T17:14:00Z) No Entry 2 List(2025-05-18T17:34:45Z, 2025-05-18T17:35:15Z) Pass 6 List(2025-05-18T17:20:05Z, 2025-05-18T17:20:35Z) Out of Business 5 List(2025-05-18T17:20:25Z, 2025-05-18T17:20:55Z) Pass 4 List(2025-05-18T17:33:50Z, 2025-05-18T17:34:20Z) Pass w/ Conditions 4 List(2025-05-18T17:02:40Z, 2025-05-18T17:03:10Z) Fail 1 List(2025-05-18T17:13:45Z, 2025-05-18T17:14:15Z) Fail 1 List(2025-05-18T17:22:10Z, 2025-05-18T17:22:40Z) No Entry 3 List(2025-05-18T17:18:35Z, 2025-05-18T17:19:05Z) Pass 9 List(2025-05-18T16:58:00Z, 2025-05-18T16:58:30Z) Pass w/ Conditions 2 List(2025-05-18T17:30:55Z, 2025-05-18T17:31:25Z) No Entry 3 List(2025-05-18T17:14:10Z, 2025-05-18T17:14:40Z) Fail 2 List(2025-05-18T17:28:20Z, 2025-05-18T17:28:50Z) Pass w/ Conditions 1 List(2025-05-18T17:14:00Z, 2025-05-18T17:14:30Z) Pass 8 List(2025-05-18T17:21:25Z, 2025-05-18T17:21:55Z) Pass 3 List(2025-05-18T17:14:30Z, 2025-05-18T17:15:00Z) Out of Business 5 List(2025-05-18T17:23:10Z, 2025-05-18T17:23:40Z) Not Ready 1 List(2025-05-18T17:29:55Z, 2025-05-18T17:30:25Z) Out of Business 5 List(2025-05-18T17:32:25Z, 2025-05-18T17:32:55Z) No Entry 1 List(2025-05-18T16:56:20Z, 2025-05-18T16:56:50Z) Pass 6 List(2025-05-18T17:17:30Z, 2025-05-18T17:18:00Z) Not Ready 2 List(2025-05-18T17:19:35Z, 2025-05-18T17:20:05Z) Pass w/ Conditions 4 List(2025-05-18T17:12:40Z, 2025-05-18T17:13:10Z) Fail 1 List(2025-05-18T17:13:25Z, 2025-05-18T17:13:55Z) Pass w/ Conditions 1 List(2025-05-18T17:20:40Z, 2025-05-18T17:21:10Z) Fail 2 List(2025-05-18T17:12:10Z, 2025-05-18T17:12:40Z) Fail 3 List(2025-05-18T17:13:35Z, 2025-05-18T17:14:05Z) Pass w/ Conditions 3 List(2025-05-18T17:01:45Z, 2025-05-18T17:02:15Z) Out of Business 7 List(2025-05-18T17:33:00Z, 2025-05-18T17:33:30Z) Pass w/ Conditions 1 List(2025-05-18T16:55:50Z, 2025-05-18T16:56:20Z) Out of Business 3 List(2025-05-18T17:02:00Z, 2025-05-18T17:02:30Z) Pass 8 List(2025-05-18T16:58:45Z, 2025-05-18T16:59:15Z) Pass 10 List(2025-05-18T17:33:40Z, 2025-05-18T17:34:10Z) No Entry 1 List(2025-05-18T17:20:20Z, 2025-05-18T17:20:50Z) Out of Business 4 List(2025-05-18T17:11:30Z, 2025-05-18T17:12:00Z) Pass w/ Conditions 3 List(2025-05-18T17:31:55Z, 2025-05-18T17:32:25Z) Fail 2 List(2025-05-18T17:18:00Z, 2025-05-18T17:18:30Z

# Ejercicio 10a
1. **Actualiza la columna `Results` de la tabla delta de food inspections creada en el ejercicio 1 con el valor `No result`**
2. **Ahora que tenemos la tabla delta corrompida con el valor `No result`, vamos a resolver el problema con los datos que nos llegan de Kafka, los cuales vamos a suponer como verdad absoluta, y por tanto tendremos que actualizar en tiempor real conforme vayan llegando elementos en Kafka**.<br>

---

Se aconseja para todos los streams anteriores ya que el de este ejercicio suele hacer un uso intensivo de los recursos

In [0]:
# Utilidad para resetear el checkpoint
checkpoint_path = "/tmp/project_spark/_checkpoint"

dbutils.fs.rm(checkpoint_path, True)

spark.conf.set("spark.sql.streaming.checkpointLocation", checkpoint_path)
spark.conf.get("spark.sql.streaming.checkpointLocation")

'/tmp/project_spark/_checkpoint'

In [0]:
# Corrompemos la tabla
from delta.tables import DeltaTable

# La tabla debe existir (ejecutar ejercicio 1)
inspections_table = DeltaTable.forName(spark, "food_inspections")
inspections_table.update(set = { "Results": lit("No result") } )

In [0]:
%sql
SELECT Inspection_ID, Results FROM food_inspections LIMIT 10

Inspection_ID Results 2373596 No result 2373587 No result 2373578 No result 2373575 No result 2373576 No result 2373547 No result 2373543 No result 2373523 No result 2373490 No result 2373485 No result

In [0]:
# Tenemos el stream preparado en el ejercicio 7, cambiamos un poco el df con las columnas cambiadas de nombre
inspections_to_fix_stream = inspections_kafka_df \
  .selectExpr("CAST(value AS STRING)") \
  .withColumn("value", from_json("value", schema)) \
  .select(col('value.*')) \
  .withColumn("Inspection ID", col("Inspection ID").cast("int")) \
  .withColumn("License #", col("License #").cast("int")) \
  .withColumn("Zip", col("Zip").cast("int")) \
  .withColumn("Latitude", col("Latitude").cast("double")) \
  .withColumn("Longitude", col("Longitude").cast("double")) \
  .withColumn("Inspection Date", to_date(col("Inspection Date"), "MM/dd/yyyy")) \
  .withColumnsRenamed(
    {
      "Inspection ID": "Inspection_ID",
      "DBA Name": "DBA_Name",
      "AKA Name": "AKA_Name",
      "License #": "License",
      "Facility Type": "Facility_Type",
      "Inspection Date": "Inspection_Date",
      "Inspection Type": "Inspection_Type",
    }
  )
  

Hice el ejercicio 10b antes que este, dejo el mismo comentario:

Para esta parte me ha parecido muy interesante esta parte de la documentación https://docs.databricks.com/gcp/en/structured-streaming/delta-lake#upsert-from-streaming-queries-using-foreachbatch que habla de actualizar o insertar en la tabla desde un streaming mediante el método foreachbatch.

In [0]:
from delta.tables import DeltaTable
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number, col

# Como los datos se repiten, tenemos que "deduplicarlos"
def deduplicate(batch_df):
    window = Window.partitionBy("Inspection_ID").orderBy(col("Inspection_Date").desc())
    return batch_df.withColumn("rn", row_number().over(window)) \
                   .filter("rn = 1") \
                   .drop("rn")

# Esta función sirve para hacer un upsert de los datos que vienen del stream a nuestra tabla delta
def upsert_to_delta(microBatchOutputDF, _):
  # Se asume que existe la tabla delta de destino
  micro_batch_deduplicated = deduplicate(microBatchOutputDF)
  inspections_table = DeltaTable.forName(spark, "food_inspections")
  inspections_table.alias("t").merge(
      micro_batch_deduplicated.alias("s"), 
      "s.Inspection_ID = t.Inspection_ID"
    ) \
    .whenMatchedUpdateAll() \
    .whenNotMatchedInsertAll() \
    .execute()

# Pasamos la función al método foreachBatch y simulamos tiempo real bajando el trigger de procesamiento
inspections_to_fix_stream.writeStream \
  .foreachBatch(upsert_to_delta) \
  .outputMode("update") \
  .trigger(processingTime="5 seconds") \
  .start()

Existen varias maneras de comprobar este ejercicio, la que he hecho yo es con la query de abajo, viendo como el número de filas con valor distinto de `No result` va aumentando hasta llegar a 10000 filas.

Para resetearlo, ir al ejercicio 1 y volver a ejecutar drop y create table (Celdas 14, 15 y 16) aunque creo que también vale con volver a actualizar la tabla delta de la celda 56. Aquí resetear el checkpoint.

In [0]:
%sql
SELECT Inspection_ID, DBA_Name, Results FROM food_inspections WHERE Results <> 'No result'

Inspection_ID DBA_Name Results 2290819 UVA KITCHEN AND WINE BAR Pass w/ Conditions 2290829 TACOS Y TAMALES EL POLLO. Pass 2290848 DELTA SKY CLUB Pass w/ Conditions 2290852 G.N.P.H. #EIGHT, INC. Pass 2290861 CAFE FURAIBO JAPANESE RESTAURANT & SUSHI Out of Business 2290864 TONYS PANTRY MART INC. Out of Business 2290874 TACOS Y TAMALES EL POLLO INC. Out of Business 2290883 HONEY 1 BBQ Pass 2290885 MCDONALD'S RESTAURANT Pass 2290886 MADISON MINI MART Out of Business 2290901 A KARRASEL NURSERY SCHOOL AND KINDERGARTEN, INC. Out of Business 2290907 JUDAH NORTH Out of Business 2290913 MAGAL RESTAURANT Out of Business 2290914 RAYMONDS TACOS NO. 3 Fail 2290916 SMOKE DADDY Pass w/ Conditions 2290921 LINKEDIN CORPORATION Pass 2290927 LAGO BANQUETS Pass w/ Conditions 2290928 SCHWAB REHAB HOSPITAL&CARE NET Pass 2290935 MT SINAI HOSPITAL MEDICAL CTR Pass 2290939 RAINBOW BEACH SUB SHOP Fail 2290941 J & J FISH Out of Business 2290942 HIGHWAY HOUSE Pass w/ Conditions 2290949 GOLDEN APPLE RESTAURANT Pass w/ Conditions 2290952 GEN HOE Out of Business 2290956 SWEET PEPPER VENEZUELAN FOOD BAR Fail 2290958 LIMELIGHT Pass w/ Conditions 2290962 RESTAURANT PUEBLA Fail 2290965 ANTHONY D'S GRILL Out of Business 2290966 J J FISH & CHICKEN Pass 2290969 HIGHWAY HOUSE Out of Business 2290973 SUBWAY Pass w/ Conditions 2290988 SIX O SIX THE LOUNGE Fail 2290997 CHOPSTICK EXPRESS Pass w/ Conditions 2291008 SUPERMERCADO EL PARAISO INC. Not Ready 2291011 PEACE INFANTS AND TODDLER CENTER Pass 2291013 MARTINI CLUB Out of Business 2291014 LEUNG'S CHOP SUEY Out of Business 2291026 NORTH SHORE BANQUET Pass 2291030 ICE CREAM BAR INC. Pass 2291041 PICNIC WINE & PROVISIONS Fail 2291042 PETE'S Not Ready 2291044 STARBUCKS COFFEE #2334 Out of Business 2291048 312 CHICAGO STYLE FOOD Not Ready 2291059 DOUGLAS PARK DOLLAR & FOOD Pass 2291073 GORILLA SUSHI LOGAN SQUARE Fail 2291075 HEALTHY SUBSTANCE KITCHEN, LLC Pass 2291085 QDOBA MEXICAN EATS # 2154 Pass 2291101 ARGO TEA CAFE-OHARE T2 Pass 2291104 D'NUEZ Pass w/ Conditions 2291116 HITZ RESTAURANT GROUP LLC Pass w/ Conditions 2291118 DAMATO BAKERY #1 Pass 2291120 SUBWAY Pass 2291131 WENDY'S PROPERTIES,LLC Fail 2291149 SUSHI-SAN Pass w/ Conditions 2291158 DAK Pass w/ Conditions 2291162 CHINA CHEF Fail 2291166 BP Pass 2291177 4 YOLKS,INC No Entry 2291178 A.P. DELI RESTAURANT GROUP, INC. Pass w/ Conditions 2291196 YUM DUM TRUCK Pass 2291197 LIFEWAY KEFIR SHOP Pass 2291198 CARNIVALE FOOD TRUCK Pass w/ Conditions 2291204 BAGDAD BAKERY & KABOB INC Pass 2293213 JEWELL EVENTS CATERING Pass 2293215 KIDZ CREATIVE CORNER Pass 2293222 SUBWAY Pass 2293232 BIG TOP RESTAURANT Out of Business 2293241 RAS DASHEN ETHIOPIAN RESTAURANT INC Pass w/ Conditions 2293242 THE BAGEL INC Pass w/ Conditions 2293247 AFC SUSHI @ Jewel Osco #3234 Pass 2293256 THE BAD APPLE No Entry 2293271 CARRILLO'S STORE CO. Out of Business 2293279 ALDEN NURSING CENTER PRINCETON Pass 2293293 WELLNESS GRUB Out of Business 2293294 BUSOFAT AFRICAN CUISINE Pass 2293295 QUIOTE / TODOS SANTOS Fail 2293296 JAMES HOTEL CHICAGO Out of Business 2293299 JAMES HOTEL CHICAGO Out of Business 2293309 BURRITO BEACH Pass w/ Conditions 2293321 ART OF PIZZA ON STATE Not Ready 2293326 LINCOLN PARK STADIUM BAR AND GRILL Pass w/ Conditions 2293337 ABUNDANCE BAKERY Fail 2293343 JOE'S BAR Pass 2293347 SWIG No Entry 2293355 LITTLE SHEEP MONGOLIAN HOTPOT Out of Business 2293361 WIKIWIKI POKE Out of Business 2293377 THE JAMES KITCHEN & BAR Out of Business 2293386 BEST FOOD MART Out of Business 2293387 SUBWAY Pass 2293397 SUPERMERCADO LA MORELIANA Not Ready 2293402 GRILL TO CHILL INC. Pass w/ Conditions 2293405 DDANDAVIS FOOD MART Pass 2293417 BISTRO ASCIONE Fail 2293419 MCDONALDS #5471 Pass 2293425 SOUTH SHORE FOOD MART INC. Fail 2293435 FAIRPLAY FINER FOODS INC Pass 2293440 APPLEBEE'S NEIGHBORHOOD GRILL & BAR Pass 2293443 THE GODDESS GOLD COAST Pass w/ Conditions 2293447 DUNKIN DONUTS Fail 2293461 SODEXO AMERICA, LLC Pass w/ Conditions 2293464 COURAGEOUS BAKERY Out of Business 2293469 THE PURPLE PIG 

# Ejercicio 10b
Diseñar una solución de análisis en tiempo real utilizando Apache Spark en Databricks para consumir datos de vuelos transmitidos por Kafka, almacenarlos en una tabla Delta y visualizar la posición actual de los vuelos sobre un mapa.
- Los datos de los vuelos están en un topic llamado `flights`
- Guardar en una tabla delta todos los vuelos, pero sólo una entrada por código de vuelo, de manera que si recibimos actualizaciones de posiciones del vuelo, se actualizará el registro correspondiente. Esto debe suceder en tiempo real.

---

In [0]:
# Utilidad para resetear el checkpoint
checkpoint_path = "/tmp/project_spark/_checkpoint"

dbutils.fs.rm(checkpoint_path, True)

spark.conf.set("spark.sql.streaming.checkpointLocation", checkpoint_path)
spark.conf.get("spark.sql.streaming.checkpointLocation")

'/tmp/project_spark/_checkpoint'

In [0]:
KAFKA_BOOSTRAP_SERVER="35.227.18.205:9094"

In [0]:
from pyspark.sql.functions import from_json, col, to_date
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, LongType, DoubleType, BooleanType

flights_kafka_df = spark \
  .readStream \
  .format("kafka") \
  .option("kafka.bootstrap.servers", KAFKA_BOOSTRAP_SERVER) \
  .option("subscribe", "flights") \
  .option("startingOffsets", "earliest") \
  .option("maxOffsetsPerTrigger", 500) \
  .load()
  
schema_flights = StructType([
    StructField("icao24", StringType(), True),
    StructField("callsign", StringType(), True),
    StructField("origin_country", StringType(), True),
    StructField("time_position", LongType(), True),
    StructField("last_contact", LongType(), True),
    StructField("longitude", DoubleType(), True),
    StructField("latitude", DoubleType(), True),
    StructField("on_ground", BooleanType(), True),
    StructField("velocity", DoubleType(), True),
    StructField("heading", DoubleType(), True),
    StructField("squawk", StringType(), True),
    StructField("spi", BooleanType(), True),
    StructField("position_source", IntegerType(), True)
])

flights_stream = flights_kafka_df \
  .selectExpr("CAST(value AS STRING)") \
  .withColumn("value", from_json(col("value"), schema_flights)) \
  .select(col('value.*'))

In [0]:
%sql
DROP TABLE IF EXISTS flights;

In [0]:
FLIGHTS_TABLE_PATH = "/user/hive/warehouse/flights"
dbutils.fs.rm(FLIGHTS_TABLE_PATH, recurse=True)

True

Para esta parte me ha parecido muy interesante esta parte de la documentación [https://docs.databricks.com/gcp/en/structured-streaming/delta-lake#upsert-from-streaming-queries-using-foreachbatch](https://docs.databricks.com/gcp/en/structured-streaming/delta-lake#upsert-from-streaming-queries-using-foreachbatch) que habla de actualizar o insertar en la tabla desde un streaming mediante el método foreachbatch.

In [0]:
from delta.tables import DeltaTable
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number, col

# Como los datos se repiten, tenemos que "deduplicarlos"
def deduplicate(batch_df):
    window = Window.partitionBy("icao24").orderBy(col("last_contact").desc())
    return batch_df.withColumn("rn", row_number().over(window)) \
                   .filter("rn = 1") \
                   .drop("rn")

# Esta función sirve para hacer un upsert de los datos que vienen del stream a nuestra tabla delta
def upsert_to_delta(microBatchOutputDF, _):
  if not DeltaTable.isDeltaTable(spark, FLIGHTS_TABLE_PATH):
    microBatchOutputDF \
      .write \
      .format("delta") \
      .save(FLIGHTS_TABLE_PATH)
    spark.sql("CREATE TABLE flights USING DELTA LOCATION \'" + FLIGHTS_TABLE_PATH + "\'")
    return

  micro_batch_deduplicated = deduplicate(microBatchOutputDF)
  flights_table = DeltaTable.forPath(spark, FLIGHTS_TABLE_PATH)
  flights_table.alias("t").merge(
      micro_batch_deduplicated.alias("s"), 
      "s.icao24 = t.icao24"
    ) \
    .whenMatchedUpdateAll() \
    .whenNotMatchedInsertAll() \
    .execute()

# Pasamos la función al método foreachBatch y simulamos tiempo real bajando el trigger de procesamiento
flights_stream.writeStream \
  .foreachBatch(upsert_to_delta) \
  .outputMode("update") \
  .trigger(processingTime="20 seconds") \
  .start()

El resultado es un poco confuso, parece correcto pero al haber tantos datos, el mapa se ve lleno y no muy legible.

He tratado de limitar a varios ids de vuelo pero imposible, no consigo algo legible.

In [0]:
%sql
SELECT latitude, longitude from flights

latitude longitude 36.1642 -4.9265 41.2912 2.0882 41.2912 2.0882 41.8286 -2.3029 36.3159 -7.8402 37.3288 -4.1372 39.386 -4.0925 39.386 -4.0925 36.8676 -2.5789 38.6698 0.873 41.9789 -3.1259 40.9432 1.572 39.2298 -8.488 39.2298 -8.488 41.4562 -1.4792 37.6406 -0.872 39.915 -3.8963 36.587 -4.6431 39.3363 2.3046 40.9474 2.3083 40.899 -3.3455 41.3026 2.0944 38.1255 -8.6884 39.2363 -0.129 39.1641 -0.1133 39.1109 2.7453 41.3051 2.0873 40.9751 -3.7167 40.9802 -2.5011 40.9802 -2.5011 38.1134 -5.2537 38.1134 -5.2537 39.1317 -8.1522 39.1317 -8.1522 41.9333 -2.8906 41.9333 -2.8906 41.0481 -1.9284 39.6759 1.0504 39.6406 2.9512 41.5481 2.0314 39.5914 -6.1312 41.472 -5.5178 41.472 -5.5178 40.136 -2.1152 39.1066 -0.9968 39.3789 -0.6094 39.3789 -0.6094 40.8048 -2.63 40.8048 -2.63 38.9348 1.7162 41.2957 2.0595 41.2921 2.0742 41.3054 2.0881 41.3005 2.0755 41.2909 2.0763 37.3716 -4.5016 41.2999 2.7275 37.2522 -4.7969 42.7647 1.4513 42.4614 -2.5523 42.4614 -2.5523 39.8041 -5.3068 40.5824 -3.5596 39.9703 -4.3174 39.9703 -4.3174 40.7112 -2.3594 41.2946 2.0833 41.0034 1.5654 41.0034 1.5654 41.2921 2.103 41.3607 2.2645 41.2933 2.1027 41.2788 2.4059 42.1432 -1.5173 38.4257 -2.6275 38.4257 -2.6275 38.3342 -0.361 42.8562 -2.6463 41.3845 2.335 41.5582 2.1091 37.5738 -3.8444 37.5738 -3.8444 41.276 -0.6348 40.5562 -3.5595 37.5118 -5.5535 37.5118 -5.5535 41.2904 2.0711 41.2904 2.0711 41.3155 2.1327 42.5297 -8.4449 36.8447 -2.3669 41.187 0.8065 40.6297 -3.5753 41.2942 2.0972 38.9343 -5.2276 41.6882 -4.015 39.4749 -3.0507 39.4749 -3.0507 40.5573 -3.5595 39.9822 1.8009 39.2671 -8.8815 40.5501 -3.5749 40.5573 -3.5595 40.5561 -3.5595 40.9159 -3.5096 41.0588 1.8669 40.7422 -0.8169 40.7422 -0.8169 40.6319 -3.5599 40.8069 1.1906 40.4873 -3.3091 40.4873 -3.3091 41.419 -1.5656 41.419 -1.5656 38.9328 1.1169 40.6078 -3.5752 40.3408 0.7682 40.3408 0.7682 42.0334 -2.1683 36.9226 -4.5876 38.9251 0.8541 38.9251 0.8541 38.356 -7.9823 37.4213 -5.8992 37.4213 -5.8992 41.5226 -8.7224 41.5226 -8.7224 36.2571 -8.2214 41.4323 2.4767 38.916 2.1476 41.2911 2.0785 41.2911 2.0785 42.611 -1.4052 42.0625 -1.2416 42.5996 -0.7483 41.0132 2.2413 37.8343 -6.4958 42.5213 -0.6831 40.4248 -3.6331 40.1424 -3.6818 40.1424 -3.6818 39.4866 -0.4738 38.4109 -8.3079 41.293 2.0996 40.5628 -5.777 39.2501 -7.1331 36.8663 -4.3327 38.3009 -3.0322 38.3009 -3.0322 36.0256 -8.8606 39.7038 -5.6708 36.8022 -4.1365 41.2925 2.1032 40.9761 1.2371 40.7501 -1.6763 41.7532 -5.6864 42.4653 -2.8669 39.1235 -4.7791 38.8093 -4.8951 42.6786 -2.6089 42.6786 -2.6089 41.4394 -8.6548 38.4818 -3.4691 42.8499 -0.1055 42.5932 -2.6739 41.2293 -2.4604 40.9903 -3.1576 37.4213 -5.899 37.4213 -5.899 38.8744 1.3724 41.3105 -3.5568 41.2898 2.079 40.2822 -7.2151 40.8772 -6.099 41.1358 -5.9569 41.4327 -5.7584 36.0818 1.44 41.5018 1.6773 41.794 -3.1956 41.794 -3.1956 42.8778 -4.496 36.6859 -4.5122 39.4673 2.5842 38.2852 -0.5796 39.3936 2.6418 41.0018 -6.065 37.0247 -8.0338 37.0247 -8.0338 41.9022 -5.1811 41.9022 -5.1811 42.6631 1.3818 42.6631 1.3818 42.6891 -5.0713 39.491 2.6026 42.6644 -5.496 38.82 -7.7852 42.9811 0.1255 39.9614 -7.4249 40.7301 -3.576 37.9155 -5.3027 38.7559 -1.7074 39.4894 -0.4732 41.4396 -5.7042 41.2798 2.069 40.0534 -8.5186 39.9927 -7.4045 39.2314 -7.2032 39.7341 -7.0911 39.7341 -7.0911 41.3686 0.9194 40.7004 -6.2216 40.7004 -6.2216 39.0191 1.327 37.4236 -5.8973 40.7797 -4.3723 42.0854 -4.101 40.1043 2.5282 41.3347 2.1887 41.2902 2.0919 36.6812 -4.505 36.6812 -4.505 40.1587 -6.7231 40.1587 -6.7231 37.4232 -7.6488 38.9028 -7.3411 38.9819 -1.2351 38.9819 -1.2351 41.058 -6.8319 38.9202 -7.3645 40.3601 -7.3528 38.3343 -0.933 36.1519 -5.3299 36.6771 -5.9552 38.5713 -0.2514 39.6443 2.9507 36.6675 -7.7958 41.5186 -4.1581 41.4236 2.3027 41.2923 2.0981 41.1367 1.8556 40.9679 1.6073 37.5216 -7.6837 38.7154 -4.6025 42.4502 -3.3687 40.0667 -5.2819 40.0667 -5.2819 38.7229 -8.902 38.7229 -8.902 42.7397 -0.5753 42.7397 -0.5753 39.3983 2.8225 37.1314 -7.6739 37.1314 -7.6739 39.3709 -7.9861 39.3709 -7.9861 40.3362 -7.017 41.2929 1.433

Databricks visualization. Run in Databricks to view.

Para más información sobre los datos de entrada consultar [OpenSky Network](https://openskynetwork.github.io/opensky-api/rest.html#all-state-vectors). A continuación se muestra un pantallazo de la visualización que se pretende conseguir. Te en cuenta que esta visualización de mapa está disponible en Databricks, con lo que no necesitará importar ninguna librería externa

![Flight Map](https://raw.githubusercontent.com/masfworld/datahack_docker/ab487794745499248388b67cf574085c5d86746e/zeppelin/data/image.png)